#**5. gyakorlat - PH eloszlások, fluid forgalmak**



##1. PH eloszlások




1. Egy szerver minden beérkező igényt 98% eséllyel normál üzemben kiszolgál, ilyenkor a kiszolgálási ráta 1 (1/s). Azonban 2% eséllyel a szerver ,,lefagy'', ilyenkor a kiszolgálási ráta 0.01 1/s. (A lefagyás bekövetkezte az igénytől és az előzményektől független.)

  (a) Milyen eloszlású egy véletlen igény kiszolgálási ideje?

  (b) Mennyi az átlagos kiszolgálási ideje egy véletlen igénynek?

  (c) Feltéve, hogy 5s alatt nem fejeződött be a kiszolgálás, mekkora a feltételes valószínűsége, hogy a szerver lefagyott?

  (d) Azt a policy-t vezetjük be, hogy ha egy igényt 5s alatt sem szolgál ki a szerver, akkor a kiszolgálást megszakítjuk, majd újra beküldjük az igényt. Átlagosan mennyi idő telik el az első beküldéstől a kiszolgálás végéig?


In [ ]:
import sympy as sp
from IPython.display import display, Math

lambda_A, lambda_B, mu_A, mu_B = sp.symbols("lambda_A lambda_B mu_A mu_B")
t = sp.symbols("t")

# PH megadása
al = sp.Matrix([0.98, 0.02]).T
D = sp.Matrix([
    [-1, 0],
    [0, -1/100]
])

# Záróvektor
ev = sp.Matrix([1, 1])

In [ ]:
def disp(expr, val=""):
  display(Math(expr + "=" + sp.latex(val)))
  print("\n")

In [ ]:
# (a) Milyen eloszlású egy véletlen igény kiszolgálási ideje?
# Az eloszlásfüggvény képlete alapján
Ft = 1 - (al * sp.exp(D * t) * ev)[0]
disp("F(t) = 1 - \pi e^{D t}\mathbf{1}", Ft)

<IPython.core.display.Math object>

In [ ]:
# (b) Mennyi az átlagos kiszolgálási ideje egy véletlen igénynek?
EX = (al * (-D.inv()) * ev)[0]
disp("E[X] = \pi (-D)^{-1}\mathbf{1}", EX)

<IPython.core.display.Math object>

In [ ]:
# (c) Feltéve, hogy 5s alatt nem fejeződött be a kiszolgálás, mekkora a feltételes valószínűsége, hogy a szerver lefagyott?
t0 = 5
disp(r"P(\text{Lefagyott | X>5})=\frac{P(\text{Lefagyott, X>5})}{P(\text{X>5s})}=\frac{P(\text{Lefagyott, X>5})}{1 - F_X(5)}=\frac{0.02 * e^{-1/100 * 5}}{\pi e^{D * 5}\mathbf{1}}",
             sp.N(al[1] * sp.exp(D[1,1] * t0) / (1 - Ft.subs(t, t0))))

<IPython.core.display.Math object>

In [ ]:
#(d) Azt a policy-t vezetjük be, hogy ha egy igényt 5s alatt sem szolgál ki a szerver, akkor a kiszolgálást megszakítjuk, majd újra beküldjük
# Az eltelt idő két része:
#   N beküldésből N-1-szer nem sikerül időben befejezni - N geometriai eloszlású F(5) paraméterrel
#   1-szer sikerül időben befejezni - Z val. változó

# A beküldések számának várható értéke
EN = 1 / Ft.subs(t, 5)
disp("E[N]", EN)

# A sűrűségfüggvény
f = (al * sp.exp(D * t) * (-D) * ev)[0]

disp("f(t) = \pi * e^{D t}(-D)\mathbf{1}", f)
EZ = sp.N(sp.integrate(t * f, (t, 0, 5) ) / Ft.subs(t, 5))
disp(r"E[Z] = \frac{\int_{t=0}^{5}t f(t)}{P(X<5)} = \frac{\int_{t=0}^{5}t f(t)}{F(5)}", EZ)

# A fentiekből következik, hogy a teljes eltelt idő:
EY = sp.N((EN - 1) * 5 + EZ)
disp("E[Y]", EY)

<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

2. Egy üzemben két gép üzemel, A és B, melyek időnként elromlanak. Az A gép átlagosan hetente egyszer romlik el, a B gép átlagosan hetente kétszer; mindkét gép üzemideje exponenciális és független a másik géptől és az előzményektől. A javításukkal egy szerelő foglalkozik, aki egyszerre egy gépet tud javítani. Ha elromlik egy gép, egyből szerelni kezdi. Az A gépet átlagosan 18, a B gépet átlagosan 12 óra alatt javítja meg; a javítási idő exponenciális eloszlású és független az előzményektől és a másik géptől. A javítás végén a gép egyből újból üzemelni kezd.

  Egy adott időpontban mindkét gép üzemel. Adjuk meg az első olyan időpontnak az eloszlását, amikor mindkét gép leáll. Számítsuk ki a várható értékét és a szórását is.

In [ ]:
# Legyen lambda_<X> az <X> eszköz elromlási intenzitása és mu_<X> a megszerelésé
lambda_A, lambda_B, mu_A, mu_B = sp.symbols("lambda_A lambda_B mu_A mu_B")

# A működést leíró generátor mátrix
Q = sp.Matrix([
    [- (lambda_A + lambda_B), lambda_A, lambda_B, 0],
    [mu_A, -(lambda_B + mu_A), 0, lambda_B],
    [mu_B, 0, -(lambda_A + mu_B), lambda_A],
    [0, 0, 0, 0]  # Absorbing state
])

# A hozzá tartozó PH eloszlás leírása
al = sp.Matrix([1, 0, 0]).T
D = Q[:-1,:-1]

disp(r"\alpha ", al)
disp("D", D)

<IPython.core.display.Math object>

<IPython.core.display.Math object>

In [ ]:
# Helyettesítsük be a numerikus értékeket
vals = [(lambda_A, 1/7), (lambda_B, 2/7), (mu_A, 4/2), (mu_B, 2)]

D = D.subs(vals)
disp("D", D)

<IPython.core.display.Math object>

In [ ]:
# Kezdeti valószínűségek (kezdetben mindkét gép üzemel)
al = sp.Matrix([1, 0, 0]).T
# Záró vektor
ev = sp.Matrix([1, 1, 1])

# Az eloszlásfüggvény képlete alapján
EX = (al * (-D.inv()) * ev)[0]
display(Math("F(t) = 1 - \pi e^{D t}\mathbf{1}"))
print("\n")
# Várható érték
disp("E[X]=\pi (-D)^{-1}\mathbf{1}", sp.N(EX))

# Második momentum
EX2 = (2 * al * (-D)**-2 * ev)[0]
disp("E[X^2]=2 * \pi (-D)^{-2}\mathbf{1}", sp.N(EX2))

# Szórás
sig = (EX2 - EX**2) ** 0.5
disp("\sigma = \sqrt{E[X^2] - E[X]^2}", sp.N(sig))

<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

##2. Fluid forgalmak

3. Egy fluid szerver kiszolgálási sebessége 5 Mbps, és a szerverhez végtelen buffer tartozik. A szerverbe egy ON/OFF fluid forgalom érkezik, mely 2/s rátával kikapcsol, illetve 1/s rátával bekapcsol; amikor ad, akkor a sebessége 9 Mbps.

  (a) Stabil-e a sor?

  (b) Számítsuk ki az átlagos buffer szintet.

  (c) Mennyi a forgalom átlagos késleltetése?

  (d) A forgalom mekkora részének késleltetése nagyobb, mint 2s?

  (e) Számítsuk ki a stacionárius eloszlás alapján az átlagos kiszolgálási rátát.

In [ ]:
# Definiáljuk a változókat és az értéküket
lam, mu, q12, q21, x = sp.symbols("lambda mu q12 q21 x")
vals = [(lam, 9), (mu, 5), (q12, 2), (q21, 1)]

# Az órai képletek szerint
# f1(x)
f1 = q21 / (q12 + q21) * (q12/(lam - mu) - q21/mu) * sp.exp(-(q12/(lam - mu) - q21/mu) * x)
f1s = f1.subs(vals)
disp(r"f_1(x)=" + sp.latex(f1), f1s)

# f2(x)
f2 = q21 / (q12 + q21) * (q12 * mu - q21 * (lam - mu))/ mu**2 * sp.exp(-(q12/(lam - mu) - q21/mu) * x)
f2s = f2.subs(vals)
disp(r"f_2(x)=" + sp.latex(f2), f2s)
print("\n")

# l1
l1 = 0

# l2
l2 = (q12 * mu - q21 * (lam - mu)) / ((q12 + q21) * mu)
l2s = l2.subs(vals)
disp(r"l_2=" + sp.latex(l2), l2s)

<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

In [ ]:
# (a) Stabil-e a sor?
# A generátorhoz tartozó stacionárius vektor kiszámolható kézzel is
pi = sp.Matrix([q21 / (q21 + q12), q12 / (q21 + q12)])

# Az érkezési intenzitások vektora
lamv = sp.Matrix([lam, 0])

# A stabilitás feltétele
display(Math("\sum_{i=1}^{2}\pi_i \lambda_i < \mu:"))
((pi.T * lamv)[0] < mu).subs(vals)

<IPython.core.display.Math object>

True

In [ ]:
# (b) Számítsuk ki az átlagos buffer szintet
# Szükségünk lesz a végtelenre
from sympy import oo

# A várható érték általános képlete alapján
EX = sp.integrate(x*f1s, (x, 0, oo)) + sp.integrate(x*f2s, (x, 0, oo))
disp(r"E[X]=\int_{x=0}^{\infty}x f_1(x) dx + \int_{x=0}^{\infty}x f_2(x) dx", EX)

<IPython.core.display.Math object>

In [ ]:
# (c) Mennyi a forgalom átlagos késleltetése?
ET = sp.N(sp.integrate(x*f1s, (x, 0, oo)) / sp.integrate(f1s, (x, 0, oo)))
disp(r"E[T] = \frac{\int_{x=0}^{\infty} f_1(x) dx}{\int_{x=0}^{\infty} f_1(x) dx}", ET)

<IPython.core.display.Math object>

In [ ]:
# (d) A forgalom mekkora részének késleltetése nagyobb mint 2s?
disp(r"P(T > 2) = P(X > 10) = \frac{\int_{x=10}^{\infty} f_1(x) dx}{\int_{x=0}^{\infty} f_1(x) dx}",
             sp.N(sp.integrate(f1s, (x, 10, oo)) / sp.integrate(f1s, (x, 0, oo))))

<IPython.core.display.Math object>

In [ ]:
# (e) Számítsuk ki a stacionárius eloszlás alapján az átlagos kiszolgálási rátát.
(1 - l2s) * mu.subs(vals)

3

4. Egy hálózatban 3 fluid szerver van, kiszolgálási sebességük rendre 3.0, 3.5, 6.0. A hálózatban 4 különböző prioritású forgalom van jelen, csökkenő prioritási sorrendben:

    (1) az érkezési rátája 1.6, és áthalad a 2-es és 3-as szervereken;

	  (2) az érkezési rátája 2.4, és áthalad mindhárom szerveren;

	  (3) az érkezési rátája 1.3, és áthalad az 1-es és 3-as szervereken;

	  (4) az érkezési rátája 1.7, és áthalad a 3-as szerveren.

  Minden forgalomról ütközés esetén instant és tökéletes visszaszabályozást feltételezünk a hálózatba való belépési pontjukig visszamenőleg.

  Számítsuk ki, melyik forgalom mekkora sebességre áll be. Adjuk meg azt is, melyik szervernek mekkora a kihasználtsága.
